In [33]:
%pip install gensim

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.0.1 -> 24.0
[notice] To update, run: python3 -m pip install --upgrade pip


In [ ]:
from gensim.models import fastText
from gensim.test.utils import datapath

In [2]:
%pip install pandas
%pip install scipy
%pip install openpyxl

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.0.1 -> 24.0
[notice] To update, run: python3 -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.0.1 -> 24.0
[notice] To update, run: python3 -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.0.1 -> 24.0
[notice] To update, run: python3 -m pip install --upgrade pip


In [3]:
from scipy import spatial
import pandas as pd
import openpyxl as op
from openpyxl.utils.dataframe import dataframe_to_rows

In [4]:
from sklearn.neighbors import NearestNeighbors
import numpy as np

In [5]:


def saving_to_xlsx(database, filexlsx):
    wb = op.Workbook()
    ws = wb.active
    for r in dataframe_to_rows(database, index=True, header=True):
        ws.append(r)
    ws.delete_rows(2)
    for cell in ws['A'] + ws[1]:
        cell.style = 'Pandas'
    wb.save(filexlsx)
    
def read_excel_to_df(filexlsx):
    database = pd.read_excel(filexlsx, index_col=0)
    return database

def spatialDistance(vector1, vector2):
    return spatial.distance.euclidean(vector1, vector2)



In [44]:
ft = fasttext.load_facebook_model('/home/jupyter/datasphere/project/cc.ru.3002.bin')
print('Модель загрузилась')

def generateVector(sentence):
    return ft.get_sentence_vector(sentence)

AssertionError: expected (600000000,),  got (288670963,)

In [9]:
def Vectorization(path):
    df = read_excel_to_df(path) 
    print('Файл прочитан')
    print(df.head())
    df['vector'] = df['name'].apply(generateVector)
    print('Векторы  сгенерированы')
    print(df.head())
    return df


In [ ]:
df_csr = Vectorization('/home/jupyter/datasphere/project/csr.xlsx')
print('Векторы КСР сгенерированы')
print(df_csr.head())

In [11]:
def InputToVector(line):
    vector = generateVector(line)
    print('Вектор юзера сгенерирован')
    return vector

In [ ]:
# Извлекаем векторы из DataFrame
vectors = np.array(df_csr['vector'].tolist())

In [ ]:
knn = NearestNeighbors(n_neighbors=7, metric='euclidean')
knn.fit(vectors)

In [ ]:
def Check(line):
    NEW_VEC = InputToVector(line)
    # Находим ближайших соседей для нового вектора
    distances, indices = knn.kneighbors([NEW_VEC])
    print(indices)
    # Печатаем результаты
    # Для удобства выводим информацию о найденных соседях
    nearest_neighbors = df_csr.iloc[indices[0]]
    a = distances[0].tolist()
    aa = [round((1 - x) * 100) for x in a]
    nearest_neighbors['chances'] = aa
    nearest_neighbors.pop('vector')

    return nearest_neighbors


line = 'Анкер забивной М10/12x40 '
Check(line)

In [153]:
saving_to_xlsx(Check(line), '/home/jupyter/datasphere/project/TEST.xlsx')

Вектор юзера сгенерирован
Ближайшие соседи (дистанции): [[100.         100.          98.8001033   98.8001033   94.46696993
   94.46696993  94.41554899]]
                                                     name  ...                                             vector
count                                                   7  ...                                                  7
unique                                                  4  ...                                                  7
top     Анкер грунтовый забивной самораскрывающийся, о...  ...  [-0.0052653598, -0.030448455, -0.010350903, -0...
freq                                                    2  ...                                                  1

[4 rows x 3 columns]
[0.0, 0.0, 0.011998966981780308, 0.011998966981780308, 0.055330300652464734, 0.055330300652464734, 0.05584451012462297]
                                                                               name  ... chances
id                                    

In [16]:
train = read_excel_to_df('/home/jupyter/datasphere/project/train_fin_fin.xlsx')

In [17]:
print(train)

                                                name  ... ref_unit
id                                                    ...         
NaN  DIN -рейка оцинкованная ТН35-7.5 100 см (Chint)  ...   100 шт
NaN              Анкерный элемент ТехноНиколь 8*45мм  ...       шт
NaN               Анкер забивной М10 DRM 12x40 сталь  ...       шт
NaN                         Анкер забивной М10/12x40  ...       шт
NaN                     Анкер забивной М8 LAZ латунь  ...       шт
..                                               ...  ...      ...
NaN                      Межкомнатные двери 900х2000  ...       шт
NaN                Кремнийорганическая эмаль КО-8104  ...        т
NaN                Кремнийорганическая эмаль КО-8104  ...        т
NaN                Кремнийорганическая эмаль КО-8104  ...        т
NaN                             Эмаль ПФ - 115 белая  ...       кг

[4814 rows x 4 columns]


In [18]:
train = train.reset_index(drop=True)

In [19]:
print(train.head())

                                              name  ... ref_unit
0  DIN -рейка оцинкованная ТН35-7.5 100 см (Chint)  ...   100 шт
1              Анкерный элемент ТехноНиколь 8*45мм  ...       шт
2               Анкер забивной М10 DRM 12x40 сталь  ...       шт
3                         Анкер забивной М10/12x40  ...       шт
4                     Анкер забивной М8 LAZ латунь  ...       шт

[5 rows x 4 columns]


In [23]:
def RUN_TEST(train):
    train['chances'] = np.nan
    train['sug_name'] = np.nan
    train['sug_id'] = np.nan

    for i in range(len(train)):
        line = train.iloc[i]['name']
        df = Check(line)
        print(line)
        print(df.head())
        df.reset_index(drop= False , inplace= True )
        train.loc[i, 'chances'] = df.iloc[0]['chances']
        train.loc[i, 'sug_name'] = df.iloc[0]['name']
        train.loc[i, 'sug_id'] = df.iloc[0]['id']

In [24]:
RUN_TEST(train)

Вектор юзера сгенерирован


<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa


DIN -рейка оцинкованная ТН35-7.5 100 см (Chint)
                                                                               name  ... chances
id                                                                                   ...        
27.32.13.111.21.1.06.10-0140-000  Кабель силовой с медными жилами ПвПнг(A)-FRHF ...  ...      90
21.1.06.10-0140                   Кабель силовой с медными жилами ПвПнг(A)-FRHF ...  ...      90
27.32.13.111.21.1.06.10-1298-000  Кабель силовой с медными жилами ПвБПнг(A)-FRHF...  ...      90
21.1.06.10-1298                   Кабель силовой с медными жилами ПвБПнг(A)-FRHF...  ...      90
27.32.13.111.21.1.06.10-1290-000  Кабель силовой с медными жилами ПвБПнг(A)-FRHF...  ...      90

[5 rows x 3 columns]
Вектор юзера сгенерирован
Анкерный элемент ТехноНиколь 8*45мм
                                                                              name  ... chances
id                                                                                  ...      

<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa
<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa


Анкер забивной М10 DRM 12x40 сталь
                                                                               name  ... chances
id                                                                                   ...        
59.1.23.09-0299                   Тройник переходный из нержавеющей стали 08Х18Н...  ...      91
24.20.40.000.59.1.23.09-0299-000  Тройник переходный из нержавеющей стали 08Х18Н...  ...      91
27.33.13.150.62.6.02.01-0509-000  Пускатель электромагнитный У3, 220В/50Гц, 1з+1...  ...      91
62.6.02.01-0509                   Пускатель электромагнитный У3, 220В/50Гц, 1з+1...  ...      91
24.20.40.000.59.1.23.09-0298-000  Тройник переходный из нержавеющей стали 08Х18Н...  ...      91

[5 rows x 3 columns]
Вектор юзера сгенерирован


...

<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa


Кремнийорганическая эмаль КО-8104
                                                                               name  ... chances
id                                                                                   ...        
14.4.04.04-0010                   Эмаль кремнийорганическая КО-811, КО-811К, цве...  ...      93
20.30.12.130.14.4.04.04-0010-000  Эмаль кремнийорганическая КО-811, КО-811К, цве...  ...      93
20.30.12.130.59.1.14.04-0168-000     Эмаль кремнийорганическая КО-814, термостойкая  ...      93
59.1.14.04-0168                      Эмаль кремнийорганическая КО-814, термостойкая  ...      93
20.30.12.130.14.4.04.04-0010-005  Эмаль кремнийорганическая термостойкая КО-811К...  ...      93

[5 rows x 3 columns]
Вектор юзера сгенерирован


<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa
<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa


Кремнийорганическая эмаль КО-8104
                                                                               name  ... chances
id                                                                                   ...        
14.4.04.04-0010                   Эмаль кремнийорганическая КО-811, КО-811К, цве...  ...      93
20.30.12.130.14.4.04.04-0010-000  Эмаль кремнийорганическая КО-811, КО-811К, цве...  ...      93
20.30.12.130.59.1.14.04-0168-000     Эмаль кремнийорганическая КО-814, термостойкая  ...      93
59.1.14.04-0168                      Эмаль кремнийорганическая КО-814, термостойкая  ...      93
20.30.12.130.14.4.04.04-0010-005  Эмаль кремнийорганическая термостойкая КО-811К...  ...      93

[5 rows x 3 columns]
Вектор юзера сгенерирован
Эмаль ПФ - 115 белая
                                                   name unit  chances
id                                                                   
20.30.12.130.14.4.04.08-0001-001     Эмаль ПФ-115 белая    т       94
20.30.12

<ipython-input-15-ce98b1aaaf9f>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nearest_neighbors['chances'] = aa


In [25]:
print(train.head())

                                              name  ...                            sug_id
0  DIN -рейка оцинкованная ТН35-7.5 100 см (Chint)  ...  27.32.13.111.21.1.06.10-0140-000
1              Анкерный элемент ТехноНиколь 8*45мм  ...  23.61.11.190.59.1.05.02-0133-000
2               Анкер забивной М10 DRM 12x40 сталь  ...                   59.1.23.09-0299
3                         Анкер забивной М10/12x40  ...  24.20.40.000.59.1.23.09-0299-000
4                     Анкер забивной М8 LAZ латунь  ...                   24.3.05.16-0021

[5 rows x 7 columns]


In [26]:
saving_to_xlsx(train, '/home/jupyter/datasphere/project/Train_Test.xlsx')

In [211]:
print('Чекай файл!')

Чекай файл!
